In [ ]:
!pip install -U -q PyDrive 

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
import json
import argparse 

import numpy as np
from keras.models import Sequential, load_model
from keras.layers import LSTM, Dropout, TimeDistributed, Dense, Activation, Embedding

In [ ]:
data = []
text = ''
for i, (dirpath, dirnames, filenames) in enumerate(os.walk('/content/drive/MyDrive/FYP/Data/', topdown=False)):
    # print(i, dirpath, dirnames, filenames)
    for f in filenames: #f = name of file, not full file path 
        file_path = os.path.join(dirpath, f)
        print(file_path)
        file1 = open(file_path,"r")
        txt=file1.read()
        text = text + txt
        data.append(txt)

/content/drive/MyDrive/FYP/Data/jigs.txt
/content/drive/MyDrive/FYP/Data/morris.txt
/content/drive/MyDrive/FYP/Data/playford.txt
/content/drive/MyDrive/FYP/Data/reels A-C.txt
/content/drive/MyDrive/FYP/Data/reels D-G.txt
/content/drive/MyDrive/FYP/Data/reels H-L.txt
/content/drive/MyDrive/FYP/Data/reels M-Q.txt
/content/drive/MyDrive/FYP/Data/reels R-T.txt
/content/drive/MyDrive/FYP/Data/slip.txt
/content/drive/MyDrive/FYP/Data/waltez.txt
/content/drive/MyDrive/FYP/Data/input.txt
/content/drive/MyDrive/FYP/Data/hornpipes.txt
/content/drive/MyDrive/FYP/Data/ashover.txt
/content/drive/MyDrive/FYP/Data/reels u-z.txt


In [ ]:
data

['X: 1\nT:A and D\n% Nottingham Music Database\nS:EF\nM:4/4\nK:A\nM:6/8\nP:A\nf|"A"ecc c2f|"A"ecc c2f|"A"ecc c2f|"Bm"BcB "E7"B2f|\n"A"ecc c2f|"A"ecc c2c/2d/2|"D"efe "E7"dcB| [1"A"Ace a2:|\n [2"A"Ace ag=g||\\\nK:D\nP:B\n"D"f2f Fdd|"D"AFA f2e/2f/2|"G"g2g ecd|"Em"efd "A7"cBA|\n"D"f^ef dcd|"D"AFA f=ef|"G"gfg "A7"ABc |1"D"d3 d2e:|2"D"d3 d2||\n\n\n\nX: 2\nT:Abacus\n% Nottingham Music Database\nS:By Hugh Barwell, via Phil Rowe\nM:6/8\nK:G\n"G"g2g B^AB|d2d G3|"Em"GAB "Am"A2A|"D7"ABc "G"BAG|\n"G"g2g B^AB|d2d G2G|"Em"GAB "Am"A2G|"D7"FGA "G"G3::\n"D7"A^GA DFA|"G"B^AB G3|"A7"^c=c^c Ace|"D7"fef def|\n"G"g2g de=f|"E7"e2e Bcd|"Am"c2c "D7"Adc| [1"G"B2A G3:|\n [2"G"B2A G2F||"Em"E2E G2G|B2B e2e|"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|\n"B7"B^c^d "Em"e2e|"F#7"f2f f2e|"B7"^def BAF|"Em"E2E G2G|B2B e2e|\n"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|"B7"B^c^d "Em"e2e|\n"F#7"f2e "B7"^def |[1"Em"e3 "D7"d3:|[2"Em"e3 "E7"e3||\n\n\nX: 3\nT:The American Dwarf\n% Nottingham Music Database\nS:FTB, via EF\nM:6/8\nK:

In [ ]:
text

'X: 1\nT:A and D\n% Nottingham Music Database\nS:EF\nM:4/4\nK:A\nM:6/8\nP:A\nf|"A"ecc c2f|"A"ecc c2f|"A"ecc c2f|"Bm"BcB "E7"B2f|\n"A"ecc c2f|"A"ecc c2c/2d/2|"D"efe "E7"dcB| [1"A"Ace a2:|\n [2"A"Ace ag=g||\\\nK:D\nP:B\n"D"f2f Fdd|"D"AFA f2e/2f/2|"G"g2g ecd|"Em"efd "A7"cBA|\n"D"f^ef dcd|"D"AFA f=ef|"G"gfg "A7"ABc |1"D"d3 d2e:|2"D"d3 d2||\n\n\n\nX: 2\nT:Abacus\n% Nottingham Music Database\nS:By Hugh Barwell, via Phil Rowe\nM:6/8\nK:G\n"G"g2g B^AB|d2d G3|"Em"GAB "Am"A2A|"D7"ABc "G"BAG|\n"G"g2g B^AB|d2d G2G|"Em"GAB "Am"A2G|"D7"FGA "G"G3::\n"D7"A^GA DFA|"G"B^AB G3|"A7"^c=c^c Ace|"D7"fef def|\n"G"g2g de=f|"E7"e2e Bcd|"Am"c2c "D7"Adc| [1"G"B2A G3:|\n [2"G"B2A G2F||"Em"E2E G2G|B2B e2e|"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|\n"B7"B^c^d "Em"e2e|"F#7"f2f f2e|"B7"^def BAF|"Em"E2E G2G|B2B e2e|\n"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|"B7"B^c^d "Em"e2e|\n"F#7"f2e "B7"^def |[1"Em"e3 "D7"d3:|[2"Em"e3 "E7"e3||\n\n\nX: 3\nT:The American Dwarf\n% Nottingham Music Database\nS:FTB, via EF\nM:6/8\nK:D

In [ ]:
BATCH_SIZE = 207
SEQ_LENGTH = 64

def read_batches(T, vocab_size):
    length = T.shape[0]; 
    batch_chars = int(length / BATCH_SIZE);

    for start in range(0, batch_chars - SEQ_LENGTH, SEQ_LENGTH):
        X = np.zeros((BATCH_SIZE, SEQ_LENGTH))
        Y = np.zeros((BATCH_SIZE, SEQ_LENGTH, vocab_size)) 
        for batch_idx in range(0, BATCH_SIZE): 
            for i in range(0, SEQ_LENGTH): 
                X[batch_idx, i] = T[batch_chars * batch_idx + start + i] # 
                Y[batch_idx, i, T[batch_chars * batch_idx + start + i + 1]] = 1
        yield X, Y

In [ ]:
def build_model(batch_size, seq_len, vocab_size, activation_function):
    model = Sequential()
    model.add(Embedding(vocab_size, 512, batch_input_shape=(batch_size, seq_len)))
    for i in range(4):
        model.add(LSTM(256, return_sequences=True, stateful=True))
        model.add(Dropout(0.2))

    model.add(TimeDistributed(Dense(vocab_size))) 
    model.add(Activation(activation_function))
    return model

In [ ]:
char_to_idx = { ch: i for (i, ch) in enumerate(sorted(list(set(text)))) }
print("Number of unique characters: " + str(len(char_to_idx))) #95
    
with open('/content/drive/MyDrive/FYP/char_to_idx.json', 'w') as f:
  json.dump(char_to_idx, f)

idx_to_char = { i: ch for (ch, i) in char_to_idx.items() }
vocab_size = len(char_to_idx)


Number of unique characters: 95


In [ ]:
epochs = 100

In [ ]:
model_softmax = build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size, 'softmax')
model_softmax.summary()
model_softmax.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

T = np.asarray([char_to_idx[c] for c in text], dtype=np.int32) 

print("Length of text:" + str(T.size)) 

steps_per_epoch = (len(text) / BATCH_SIZE - 1) / SEQ_LENGTH  

loss_softmax = []
accuracy_softmax = []

for epoch in range(epochs):
  print('\nEpoch {}/{}'.format(epoch + 1, epochs))
  
  losses, accs = [], []

  for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
    loss, acc = model_softmax.train_on_batch(X, Y)
    print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
    losses.append(loss)
    accs.append(acc)
  loss_softmax.append(losses)
  accuracy_softmax.append(accs)

Streaming output truncated to the last 5000 lines.
Batch 52: loss = 0.5553629398345947, acc = 0.818463146686554
Batch 53: loss = 0.5423448085784912, acc = 0.8235205411911011
Batch 54: loss = 0.5678755640983582, acc = 0.8177083134651184
Batch 55: loss = 0.5659943222999573, acc = 0.8168780207633972
Batch 56: loss = 0.573715329170227, acc = 0.8170289993286133
Batch 57: loss = 0.5986500382423401, acc = 0.8084993958473206
Batch 58: loss = 0.5645506978034973, acc = 0.8158212304115295
Batch 59: loss = 0.5520781874656677, acc = 0.820652186870575
Batch 60: loss = 0.5912842154502869, acc = 0.8102355003356934
Batch 61: loss = 0.5896297693252563, acc = 0.8154438138008118
Batch 62: loss = 0.5757076144218445, acc = 0.8130283951759338
Batch 63: loss = 0.5383007526397705, acc = 0.8248792290687561
Batch 64: loss = 0.5335795283317566, acc = 0.824577271938324
Batch 65: loss = 0.594970703125, acc = 0.8075181245803833
Batch 66: loss = 0.5803518891334534, acc = 0.8143116235733032
Batch 67: loss = 0.57130950

In [ ]:
print(loss_softmax)
print(accuracy_softmax)

[[4.554461479187012, 4.5420613288879395, 4.499406814575195, 4.311678409576416, 4.0092315673828125, 3.896613121032715, 3.927300453186035, 3.8696529865264893, 3.767822027206421, 3.7434170246124268, 3.7870798110961914, 3.7683866024017334, 3.763735055923462, 3.7329626083374023, 3.7069320678710938, 3.7251265048980713, 3.7263872623443604, 3.7073862552642822, 3.6448211669921875, 3.661818742752075, 3.6411969661712646, 3.606769561767578, 3.6638283729553223, 3.65983247756958, 3.5589303970336914, 3.578303337097168, 3.5779950618743896, 3.60075044631958, 3.541656732559204, 3.5288233757019043, 3.5375208854675293, 3.564859390258789, 3.5218114852905273, 3.5146119594573975, 3.5038793087005615, 3.4721059799194336, 3.4899814128875732, 3.4838740825653076, 3.48498272895813, 3.4622914791107178, 3.4675567150115967, 3.4643750190734863, 3.4696173667907715, 3.464007616043091, 3.4473416805267334, 3.434244155883789, 3.4438841342926025, 3.413501739501953, 3.4016833305358887, 3.3915927410125732, 3.4025330543518066,

In [ ]:
model_sigmoid = build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size, 'sigmoid')
model_sigmoid.summary()
model_sigmoid.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

T = np.asarray([char_to_idx[c] for c in text], dtype=np.int32) 

print("Length of text:" + str(T.size)) 

steps_per_epoch = (len(text) / BATCH_SIZE - 1) / SEQ_LENGTH  

loss_sigmoid = []
accuracy_sigmoid = []

for epoch in range(epochs):
  print('\nEpoch {}/{}'.format(epoch + 1, epochs))
  
  losses, accs = [], []

  for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
    loss, acc = model_sigmoid.train_on_batch(X, Y)
    print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
    losses.append(loss)
    accs.append(acc)
  loss_sigmoid.append(losses)
  accuracy_sigmoid.append(accs)

Streaming output truncated to the last 5000 lines.
Batch 52: loss = 0.5890859961509705, acc = 0.8121980428695679
Batch 53: loss = 0.576329231262207, acc = 0.8148399591445923
Batch 54: loss = 0.5839061737060547, acc = 0.8145380616188049
Batch 55: loss = 0.5902792811393738, acc = 0.811292290687561
Batch 56: loss = 0.5931491851806641, acc = 0.8114432096481323
Batch 57: loss = 0.6143658757209778, acc = 0.8046497702598572
Batch 58: loss = 0.5928484797477722, acc = 0.8097071051597595
Batch 59: loss = 0.584360659122467, acc = 0.8125
Batch 60: loss = 0.6182447075843811, acc = 0.8039703965187073
Batch 61: loss = 0.6058465838432312, acc = 0.8068387508392334
Batch 62: loss = 0.6054478883743286, acc = 0.8117451667785645
Batch 63: loss = 0.5605130195617676, acc = 0.8180857300758362
Batch 64: loss = 0.545460045337677, acc = 0.8222373127937317
Batch 65: loss = 0.6029193997383118, acc = 0.8032155632972717
Batch 66: loss = 0.5963053107261658, acc = 0.8078200221061707
Batch 67: loss = 0.5919255614280701

In [ ]:
print(loss_sigmoid)
print(accuracy_sigmoid) 

[[4.553907871246338, 4.5378336906433105, 4.468953609466553, 4.177958011627197, 4.07036018371582, 3.9272336959838867, 3.937152147293091, 3.8864235877990723, 3.8069803714752197, 3.7766497135162354, 3.7974023818969727, 3.7881710529327393, 3.793428421020508, 3.741364002227783, 3.707258701324463, 3.767049551010132, 3.754223585128784, 3.7618019580841064, 3.7326347827911377, 3.7234408855438232, 3.7423784732818604, 3.707136869430542, 3.733093023300171, 3.742532253265381, 3.6946089267730713, 3.709141254425049, 3.7243993282318115, 3.756718873977661, 3.7136428356170654, 3.7169172763824463, 3.7302348613739014, 3.751830816268921, 3.71431303024292, 3.706655979156494, 3.7213006019592285, 3.7032229900360107, 3.723205089569092, 3.7102091312408447, 3.706644296646118, 3.7043938636779785, 3.713615894317627, 3.7262048721313477, 3.741637945175171, 3.721470355987549, 3.6837940216064453, 3.6931610107421875, 3.691349744796753, 3.6700687408447266, 3.681845188140869, 3.6634933948516846, 3.6269752979278564, 3.624

In [ ]:
import pandas as pd
import statistics

In [ ]:
softmax = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in loss_softmax:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

softmax['softmax_avg'] = loss_avg
softmax['softmax_median'] = loss_median
softmax['softmax_std'] = loss_std
softmax['softmax_var'] = loss_variance
softmax['softmax_max'] = loss_max
softmax['softmax_min'] = loss_min



In [ ]:
softmax.keys()

dict_keys(['softmax_avg', 'softmax_median', 'softmax_std', 'softmax_var', 'softmax_max', 'softmax_min'])

In [ ]:
sigmoid = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in loss_sigmoid:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

sigmoid['sigmoid_avg'] = loss_avg
sigmoid['sigmoid_median'] = loss_median
sigmoid['sigmoid_std'] = loss_std
sigmoid['sigmoid_var'] = loss_variance
sigmoid['sigmoid_max'] = loss_max
sigmoid['sigmoid_min'] = loss_min

In [ ]:
sigmoid.keys()

dict_keys(['sigmoid_avg', 'sigmoid_median', 'sigmoid_std', 'sigmoid_var', 'sigmoid_max', 'sigmoid_min'])

In [ ]:
pd1 = pd.DataFrame(softmax, columns=softmax.keys() )
pd1

softmax_avg  softmax_median  ...  softmax_max  softmax_min
0      3.280537        3.274272  ...     4.554461     2.676888
1      2.222986        2.194451  ...     3.266632     1.803421
2      1.671975        1.659750  ...     2.683015     1.483692
3      1.453428        1.446275  ...     2.346617     1.322200
4      1.327703        1.323971  ...     2.143283     1.226230
..          ...             ...  ...          ...          ...
95     0.506978        0.502159  ...     1.031381     0.466550
96     0.505082        0.501910  ...     1.020387     0.467103
97     0.503820        0.498507  ...     1.005529     0.462566
98     0.503877        0.498381  ...     1.030767     0.466169
99     0.503081        0.499297  ...     1.016971     0.463068

[100 rows x 6 columns]

In [ ]:
pd2 = pd.DataFrame(sigmoid, columns=sigmoid.keys() )
pd2

sigmoid_avg  sigmoid_median  ...  sigmoid_max  sigmoid_min
0      3.455427        3.414622  ...     4.553908     2.922165
1      2.436812        2.393014  ...     3.347174     1.975161
2      1.820975        1.807117  ...     2.822812     1.603915
3      1.553680        1.543002  ...     2.341314     1.406066
4      1.398881        1.394161  ...     2.135212     1.283875
..          ...             ...  ...          ...          ...
95     0.529068        0.525025  ...     1.010996     0.477717
96     0.527568        0.523673  ...     1.020368     0.492557
97     0.524860        0.521450  ...     1.016079     0.481990
98     0.525059        0.520912  ...     1.011309     0.486322
99     0.523581        0.518333  ...     1.013207     0.479850

[100 rows x 6 columns]

In [ ]:
loss_exp = pd.concat([pd1, pd2],axis=1 )
loss_exp

softmax_avg  softmax_median  ...  sigmoid_max  sigmoid_min
0      3.280537        3.274272  ...     4.553908     2.922165
1      2.222986        2.194451  ...     3.347174     1.975161
2      1.671975        1.659750  ...     2.822812     1.603915
3      1.453428        1.446275  ...     2.341314     1.406066
4      1.327703        1.323971  ...     2.135212     1.283875
..          ...             ...  ...          ...          ...
95     0.506978        0.502159  ...     1.010996     0.477717
96     0.505082        0.501910  ...     1.020368     0.492557
97     0.503820        0.498507  ...     1.016079     0.481990
98     0.503877        0.498381  ...     1.011309     0.486322
99     0.503081        0.499297  ...     1.013207     0.479850

[100 rows x 12 columns]

In [ ]:
loss_exp.to_csv(r'/content/drive/MyDrive/FYP/Evaluation/loss_exp.csv', index = True, index_label='Epocs')

In [ ]:
softmax = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in accuracy_softmax:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

softmax['softmax_avg'] = loss_avg
softmax['softmax_median'] = loss_median
softmax['softmax_std'] = loss_std
softmax['softmax_var'] = loss_variance
softmax['softmax_max'] = loss_max
softmax['softmax_min'] = loss_min


In [ ]:
sigmoid = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in accuracy_sigmoid:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

sigmoid['sigmoid_avg'] = loss_avg
sigmoid['sigmoid_median'] = loss_median
sigmoid['sigmoid_std'] = loss_std
sigmoid['sigmoid_var'] = loss_variance
sigmoid['sigmoid_max'] = loss_max
sigmoid['sigmoid_min'] = loss_min

In [ ]:
pd1 = pd.DataFrame(softmax, columns=softmax.keys() )
pd1

softmax_avg  softmax_median  ...  softmax_max  softmax_min
0      0.156324        0.145229  ...     0.256416     0.007020
1      0.381878        0.389342  ...     0.495094     0.195803
2      0.516672        0.518569  ...     0.569595     0.361941
3      0.565905        0.566350  ...     0.604544     0.427536
4      0.595571        0.596241  ...     0.629982     0.466108
..          ...             ...  ...          ...          ...
95     0.835652        0.836277  ...     0.848732     0.741999
96     0.836405        0.837258  ...     0.849562     0.740716
97     0.837003        0.837938  ...     0.850543     0.744565
98     0.836365        0.837107  ...     0.846996     0.740263
99     0.836807        0.837334  ...     0.850091     0.742905

[100 rows x 6 columns]

In [ ]:
pd2 = pd.DataFrame(sigmoid, columns=sigmoid.keys() )
pd2

sigmoid_avg  sigmoid_median  ...  sigmoid_max  sigmoid_min
0      0.136400        0.129604  ...     0.213693     0.015399
1      0.334426        0.342920  ...     0.453955     0.169611
2      0.480603        0.480827  ...     0.539251     0.333862
3      0.541603        0.542572  ...     0.582729     0.413421
4      0.579033        0.579635  ...     0.616168     0.455767
..          ...             ...  ...          ...          ...
95     0.828686        0.829408  ...     0.843373     0.739432
96     0.829155        0.829559  ...     0.842240     0.735507
97     0.830196        0.830918  ...     0.843901     0.735734
98     0.829925        0.831220  ...     0.842089     0.741470
99     0.830373        0.831824  ...     0.842165     0.736790

[100 rows x 6 columns]

In [ ]:
accuracy_exp = pd.concat([pd1, pd2],axis=1 )
accuracy_exp

softmax_avg  softmax_median  ...  sigmoid_max  sigmoid_min
0      0.156324        0.145229  ...     0.213693     0.015399
1      0.381878        0.389342  ...     0.453955     0.169611
2      0.516672        0.518569  ...     0.539251     0.333862
3      0.565905        0.566350  ...     0.582729     0.413421
4      0.595571        0.596241  ...     0.616168     0.455767
..          ...             ...  ...          ...          ...
95     0.835652        0.836277  ...     0.843373     0.739432
96     0.836405        0.837258  ...     0.842240     0.735507
97     0.837003        0.837938  ...     0.843901     0.735734
98     0.836365        0.837107  ...     0.842089     0.741470
99     0.836807        0.837334  ...     0.842165     0.736790

[100 rows x 12 columns]

In [ ]:
accuracy_exp.to_csv(r'/content/drive/MyDrive/FYP/Evaluation/accuracy_exp.csv', index = True, index_label='Epocs')